In this iPython notebook, we will featurize MOR ligand binding simulation by pairwise distances between the ligand and different receptor residues. We will then perform tICA and prospectively build an MSM. 

In [1]:
from PDB_Order_Fixer import PDB_Order_Fixer
import mdtraj as md
import os
import numpy as np
import h5py

import datetime
import glob
import copy
from functools import partial 
import operator
import time

import random 
import subprocess
from subprocess import Popen
import sys
from io_functions import *
from custom_clusterer import *
from custom_tica import *
from custom_featurizer import *
from pdb_editing import *
from analysis import *
from io_functions import *
#from topology_fixing import *
from subsampling import *
from conversions import *
from custom_msm import *
from grids import *
from docking_analysis import *

Couldn't import dot_parser, loading of dot files will not be possible.


/home/enf/software/anaconda/lib/python2.7/site-packages/pandas/computation/__init__.py:19: UserWarning: The installed version of numexpr 2.4.4 is not supported in pandas and will be not be used

  UserWarning)


In [2]:
%matplotlib inline

import matplotlib.pyplot as plt

#set_palette('Set1', n_colors=15, desat=None)

In [8]:
samples_dir = "/home/enf/tlr8_analysis/receptors"
if not os.path.exists(samples_dir): os.makedirs(samples_dir)

In [16]:
import grids
reload(grids)
from grids import *

grid_center = "33.29, -8.42, 47.4"
active_ref_dir = "/home/enf/tlr8_analysis/4qc0_oneligand.pdb"
lig_dir = "/home/enf/tlr8_analysis/ligands"
chosen_receptors = ["4qc0_oneligand"]

#prepare_ligands(lig_dir, [".mol"])
ligands = get_ligands(lig_dir)
print(ligands)

reimaged_dir = samples_dir
mae_dir = reimaged_dir
#remove_ter(reimaged_dir)
#reorder(reimaged_dir)

grid_dir = "/home/enf/tlr8_analysis/grids"
docking_dir = "/home/enf/tlr8_analysis/docking"
if not os.path.exists(grid_dir):
    os.makedirs(grid_dir)
if not os.path.exists(docking_dir):
    os.makedirs(docking_dir)

#pprep(mae_dir, ref = active_ref_dir, chosen_receptors = chosen_receptors, worker_pool=None, parallel=True)
#generate_grids(mae_dir, grid_center, grid_dir, remove_lig = "XG1", chosen_receptors = chosen_receptors, worker_pool=None)
#unzip_receptors(grid_dir, chosen_receptors, worker_pool=None)

dock_ligands_and_receptors(grid_dir, docking_dir, lig_dir, precision = "SP", ext = "-out.maegz", chosen_ligands = ligands, chosen_receptors = chosen_receptors, parallel = "ligand", grid_ext = ".zip", worker_pool=None)



[]
ligands
['/home/enf/tlr8_analysis/ligands/3M052-out.maegz', '/home/enf/tlr8_analysis/ligands/CL307-out.maegz', '/home/enf/tlr8_analysis/ligands/CL307_SMCC-out.maegz', '/home/enf/tlr8_analysis/ligands/R848-out.maegz', '/home/enf/tlr8_analysis/ligands/Tandem782-out.maegz', '/home/enf/tlr8_analysis/ligands/Tandem782_SATA_NHS-out.maegz', '/home/enf/tlr8_analysis/ligands/Tandem782_SATA_reacted_amine-out.maegz', '/home/enf/tlr8_analysis/ligands/Tandem783-out.maegz', '/home/enf/tlr8_analysis/ligands/Tandem784-out.maegz', '/home/enf/tlr8_analysis/ligands/Tandem785-out.maegz', '/home/enf/tlr8_analysis/ligands/Tandem785_SMCC-out.maegz', '/home/enf/tlr8_analysis/ligands/Tandem785_SMCC2-out.maegz', '/home/enf/tlr8_analysis/ligands/Tandem786-out.maegz']
parallelize over ligands.
[('/home/enf/tlr8_analysis/grids', '/home/enf/tlr8_analysis/docking/3M052', '/home/enf/tlr8_analysis/ligands/3M052-out.maegz', 'SP', ['4qc0_oneligand'], False, '.zip'), ('/home/enf/tlr8_analysis/grids', '/home/enf/tlr8_a

In [20]:
import analysis
reload(analysis)
from analysis import *
docking_multiple_ligands = "%s/all_docking_scores.csv" % docking_dir
aggregate_docking = "%s/aggregate_docking.csv" % docking_dir

analyze_docking_results_multiple(docking_dir, precision = "SP", ligands = ligands, summary = docking_multiple_ligands, redo = True)
#compute_cluster_averages(None, csv_filename=docking_multiple_ligands, save_csv=aggregate_docking)


Analyzing docking results
/home/enf/tlr8_analysis/docking
[]
/home/enf/tlr8_analysis/docking/Tandem785
/home/enf/tlr8_analysis/docking/R848
/home/enf/tlr8_analysis/docking/Tandem782_SATA_NHS
/home/enf/tlr8_analysis/docking/Tandem782
/home/enf/tlr8_analysis/docking/CL307_SMCC
/home/enf/tlr8_analysis/docking/Tandem786
/home/enf/tlr8_analysis/docking/Tandem785_SMCC
/home/enf/tlr8_analysis/docking/3M052
/home/enf/tlr8_analysis/docking/Tandem783
/home/enf/tlr8_analysis/docking/Tandem784
/home/enf/tlr8_analysis/docking/Tandem785_SMCC2
/home/enf/tlr8_analysis/docking/CL307
/home/enf/tlr8_analysis/docking/Tandem782_SATA_reacted_amine
['Tandem785', 'R848', 'Tandem782_SATA_NHS', 'Tandem782', 'CL307_SMCC', 'Tandem786', 'Tandem785_SMCC', '3M052', 'Tandem783', 'Tandem784', 'Tandem785_SMCC2', 'CL307', 'Tandem782_SATA_reacted_amine']
currently analyzing Tandem785
currently analyzing R848
currently analyzing Tandem782_SATA_NHS
currently analyzing Tandem782
currently analyzing CL307_SMCC
currently anal

In [27]:
df = pd.read_csv(docking_multiple_ligands, index_col=0, skip_blank_lines=True).dropna()

In [29]:
df.transpose().sort("4qc0_oneligand", inplace=False)

/vspdata/vspcompute/home/enf/software/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:1: FutureWarning: sort(columns=....) is deprecated, use sort_values(by=.....)
  if __name__ == '__main__':


sample                          4qc0_oneligand
 CL307_SMCC                              -0.00
 3M052                                    4.31
 Tandem785_SMCC2                          5.39
 Tandem785_SMCC                           5.56
 Tandem782_SATA_reacted_amine             5.84
 Tandem782_SATA_NHS                       5.92
 Tandem782                                5.93
 R848                                     5.99
 Tandem783                                6.81
 Tandem785                                7.27
 Tandem784                                7.47
 Tandem786                                7.72
 CL307                                    8.09

In [25]:
df_agg = pd.read_csv(aggregate_docking)
aggs = df_agg.sort([' nebivolol'], ascending=[0])
aggs.iloc[0:10]
ranked = aggs.rank(axis=0, method='average', ascending=False)

In [26]:
ranked.iloc[0:10]

Unnamed: 0   isoetharine   r_isopreterenol   3p0g_lig   r_epinephrine  \
78          21            21                54         19              77   
18          81            12                40          2              21   
37          62            60                64         10              42   
7           92            20                20         17              19   
71          28            26                53         46              76   
31          68            19                31         23              27   
98           1            38                37         55              47   
74          25            18                17         11              10   
45          54            46                59         51              60   
0          100            27                33         39              55   

     nebivolol   s-carvedilol   xamoterol   procaterol   
78           1              2           2            50  
18           2             10           1            67  
37           3              3           5            53  
7            4              1           3            21  
71           5             13           8            70  
31           6              5          11            46  
98           7              4          20            64  
74           8              7          25             7  
45           9             12          17            61  
0           10             53          30            55

In [17]:
dock_ligands_and_receptors(grid_dir, docking_dir, inverse_agonist_dir, precision = precision, ext = "-out.maegz", chosen_ligands = inverse_ligands, chosen_receptors = chosen_receptors, parallel = None, grid_ext = ".grd", worker_pool=dview)

ligands
['/home/enf/b2ar_analysis/b2ar_inverse_agonists/s-atenolol-out.maegz', '/home/enf/b2ar_analysis/b2ar_inverse_agonists/s-carazolol-out.maegz']
Written all docking job input files
MAPPING OVER WORKER POOL
Done docking.
Written all docking job input files
MAPPING OVER WORKER POOL
Done docking.


In [11]:
n_clusters = 500
n_samples=10

clusterer_tICs_1_2_3_4_filename = "%s/clusterer_tICs_1_2_3_4_%dclusters_%dsamples.h5" %(tica_dir, n_clusters, n_samples)
clusterer_tICs_1_2_3_4_map_file = "%s/clusterer_tICs_1_2_3_4_%dclusters_%dsamples_map.json" %(tica_dir, n_clusters, n_samples)
tics_to_cluster = [0, 1, 2, 3]


cluster_minikmeans(tica_dir, projected_features_dir, traj_dir, n_clusters=n_clusters, clusterer_dir=clusterer_tICs_1_2_3_4_filename, tICs=tics_to_cluster)
clusterer_tICs_1_2_3_4 = verboseload(clusterer_tICs_1_2_3_4_filename)
clusterer_tICs_1_2_3_4_map = make_clusters_map(clusterer_tICs_1_2_3_4)
samples_dir = "%s/clusterer_tICs_1_2_3_4_%dclusters_%dsamples_samples" %(tica_dir, n_clusters, n_samples)
if not os.path.exists(samples_dir): os.makedirs(samples_dir)
#sample_clusters(clusterer_tICs_1_2_3_4_filename, projected_features_dir, traj_dir, traj_ext, save_dir=samples_dir, n_samples=n_samples, method = sampling_method, clusters_map_file = clusterer_tICs_1_2_3_4_map_file, tICs=[0, 1, 2, 3], worker_pool=dview)



Already clustered
loading "/home/enf/b2ar_analysis/sparse-tICA_t5_n_components25all_residues_2rh1_3sn6_under_cutoff6A_regularization_wolf_autoShrinkage_rho0pt01/clusterer_tICs_1_2_3_4_500clusters_10samples.h5"...
1388
2128
889
1989
612
1031
752
1558
1081
897
1291
2058
924
1345
1570
3006
756
1319
1114
1791
1258
1314
828
1402
380
3214
605
140
464
751
433
906
936
565
2213
414
983
1420
748
999
767
1594
673
1174
1545
1356
871
1034
1634
973
1106
1920
1421
1191
1482
1041
1618
493
958
394
643
574
753
1449
804
951
1645
210
2419
1942
1946
586
374
1344
511
845
2200
1393
1083
732
2442
2881
2008
2183
3168
795
1324
2040
1999
628
587
760
1619
1624
484
1661
1680
2099
714
1242
1372
404
821
1089
612
779
2627
580
2791
520
1192
533
930
339
2238
350
2287
1873
1528
692
766
3059
674
1611
585
450
577
436
2251
1396
609
564
368
3305
695
1083
1189
446
1505
355
632
1361
472
3769
787
2097
1664
630
731
1872
1880
590
3904
708
579
831
949
2234
1474
709
2437
1612
717
299
444
1055
730
646
1151
1083
1035
531
621
864
113

In [ ]:
grid_center = "64.4, 16.9, 11.99"

indices = [0,n_clusters]
chosen_receptors = []
for i in range(indices[0], indices[1]):
  for j in range(0, n_samples):
    chosen_receptors.append("cluster%d_sample%d" %(i, j))

biased_ligands = get_ligands(biased_agonist_dir)
print("biased_ligands")
print(biased_ligands)
reimaged_dir = samples_dir
mae_dir = reimaged_dir
#remove_ter(reimaged_dir)
#reorder(reimaged_dir)

inverse_ligands = get_ligands(inverse_agonist_dir)
agonist_ligands = get_ligands(agonist_dir)
mehrdad_dir = "%s/mehrdad_ligands" %agonist_dir

agonist_ligands = [a for a in agonist_ligands]

grid_dir =  "%s/clusterer_tICs_1_2_3_4_%dclusters_%dsamples_grids" %(tica_dir, n_clusters, n_samples)
docking_dir =  "%s/clusterer_tICs_1_2_3_4_%dclusters_%dsamples_docking" %(tica_dir, n_clusters, n_samples)

#prepare_ligands(mehrdad_dir, [".mol"])
#prepare_ligands(agonist_dir, [".sdf"])
print(mehrdad_dir)
mehrdad_ligands = get_ligands(mehrdad_dir)
print("Mehrdad ligands:")
print(mehrdad_ligands)

#pprep(mae_dir, ref = active_ref_dir, chosen_receptors = chosen_receptors, worker_pool=dview)
#generate_grids(mae_dir, grid_center, grid_dir, remove_lig = "BIA", chosen_receptors = chosen_receptors, worker_pool=dview)
#unzip_receptors(grid_dir, chosen_receptors, worker_pool=dview)

dock_ligands_and_receptors(grid_dir, docking_dir,  biased_agonist_dir, precision = precision, ext = "-out.maegz", chosen_ligands = biased_ligands, chosen_receptors = chosen_receptors, parallel = None, grid_ext = ".grd", worker_pool=dview)
dock_ligands_and_receptors(grid_dir, docking_dir, agonist_dir, precision = precision, ext = "-out.maegz", chosen_ligands = agonist_ligands, chosen_receptors = chosen_receptors, parallel = None, grid_ext = ".grd", worker_pool=dview)

#dock_ligands_and_receptors(grid_dir, docking_dir, agonist_dir, precision = precision, ext = "-out.maegz", chosen_ligands = agonist_ligands, chosen_receptors = chosen_receptors, parallel = None, grid_ext = ".grd", worker_pool=dview)

agonist_ligands = [a for a in get_ligands(agonist_dir) if "ta" not in a and "TA" not in a]
#dock_ligands_and_receptors(grid_dir, docking_dir, agonist_dir, precision = precision, ext = "-out.maegz", chosen_ligands = agonist_ligands, chosen_receptors = chosen_receptors, parallel = None, grid_ext = ".grd", worker_pool=dview)
#inverse_ligands = [lig for lig in inverse_ligands if "carazolol" in lig]
dock_ligands_and_receptors(grid_dir, docking_dir,  inverse_agonist_dir, precision = precision, ext = "-out.maegz", chosen_ligands = inverse_ligands, chosen_receptors = chosen_receptors, parallel = None, grid_ext = ".grd", worker_pool=dview)
dock_ligands_and_receptors(grid_dir, docking_dir, mehrdad_dir, precision = precision, ext = "-out.maegz", chosen_ligands = False, chosen_receptors = chosen_receptors, parallel = None, grid_ext = ".grd", worker_pool=dview)







biased_ligands
['', '', '', 'isoetharine', 'isoetharine_prepped', 'nebivolol', 's-carvedilol', 's-carvedilol_prepped', 'salmeterol', 'xamoterol']
/home/enf/b2ar_analysis/b2ar_full_agonists/mehrdad_ligands
Mehrdad ligands:
[]
5000
['/home/enf/b2ar_analysis/sparse-tICA_t5_n_components25all_residues_2rh1_3sn6_under_cutoff6A_regularization_wolf_autoShrinkage_rho0pt01/clusterer_tICs_1_2_3_4_500clusters_10samples_samples/cluster0_sample0.pdb', '/home/enf/b2ar_analysis/sparse-tICA_t5_n_components25all_residues_2rh1_3sn6_under_cutoff6A_regularization_wolf_autoShrinkage_rho0pt01/clusterer_tICs_1_2_3_4_500clusters_10samples_samples/cluster0_sample1.pdb', '/home/enf/b2ar_analysis/sparse-tICA_t5_n_components25all_residues_2rh1_3sn6_under_cutoff6A_regularization_wolf_autoShrinkage_rho0pt01/clusterer_tICs_1_2_3_4_500clusters_10samples_samples/cluster0_sample2.pdb']
Done prepping proteinsreordering /home/enf/b2ar_analysis/sparse-tICA_t5_n_components25all_residues_2rh1_3sn6_under_cutoff6A_regularizati

In [35]:
indices = [0,n_clusters]
chosen_receptors = []
for i in range(indices[0], indices[1]):
  for j in range(0, n_samples):
    chosen_receptors.append("cluster%d_sample%d" %(i, j))

biased_ligands = get_ligands(biased_agonist_dir)
print("biased_ligands")
print(biased_ligands)
reimaged_dir = samples_dir
mae_dir = reimaged_dir
remove_ter(reimaged_dir)
reorder(reimaged_dir)

inverse_ligands = get_ligands(inverse_agonist_dir)
agonist_ligands = get_ligands(agonist_dir)

agonist_ligands = [a for a in agonist_ligands if "TA" not in a and "ta" not in a]
print(agonist_ligands)

grid_dir =  "%s/clusterer_tICs_1_2_%dclusters_%dsamples_grids" %(tica_dir, n_clusters, n_samples)
docking_dir =  "%s/clusterer_tICs_1_2_%dclusters_%dsamples_docking" %(tica_dir, n_clusters, n_samples)

pprep(mae_dir, ref = active_ref_dir, chosen_receptors = chosen_receptors, worker_pool=dview)
generate_grids(mae_dir, grid_center, grid_dir, remove_lig = "BIA", chosen_receptors = chosen_receptors, worker_pool=dview)
unzip_receptors(grid_dir, chosen_receptors, worker_pool=dview)

dock_ligands_and_receptors(grid_dir, docking_dir,  biased_agonist_dir, precision = precision, ext = "-out.maegz", chosen_ligands = biased_ligands, chosen_receptors = chosen_receptors, parallel = None, grid_ext = ".grd", worker_pool=dview)
dock_ligands_and_receptors(grid_dir, docking_dir, agonist_dir, precision = precision, ext = "-out.maegz", chosen_ligands = agonist_ligands, chosen_receptors = chosen_receptors, parallel = None, grid_ext = ".grd", worker_pool=dview)

#dock_ligands_and_receptors(grid_dir, docking_dir, agonist_dir, precision = precision, ext = "-out.maegz", chosen_ligands = agonist_ligands, chosen_receptors = chosen_receptors, parallel = None, grid_ext = ".grd", worker_pool=dview)



biased_ligands
['', '', 'isoetharine', 'isoetharine_prepped', 'nebivolol', 's-carvedilol', 's-carvedilol_prepped', 'xamoterol']


reordering /home/enf/b2ar_analysis/sparse-tICA_t5_n_components25all_residues_2rh1_3sn6_under_cutoff6A_regularization_wolf_autoShrinkage_rho0pt01/clusterer_tICs_1_2_25clusters_100samples_samples/cluster12_sample71.pdb 
reordering /home/enf/b2ar_analysis/sparse-tICA_t5_n_components25all_residues_2rh1_3sn6_under_cutoff6A_regularization_wolf_autoShrinkage_rho0pt01/clusterer_tICs_1_2_25clusters_100samples_samples/cluster13_sample76.pdb 
reordering /home/enf/b2ar_analysis/sparse-tICA_t5_n_components25all_residues_2rh1_3sn6_under_cutoff6A_regularization_wolf_autoShrinkage_rho0pt01/clusterer_tICs_1_2_25clusters_100samples_samples/cluster13_sample27.pdb 
reordering /home/enf/b2ar_analysis/sparse-tICA_t5_n_components25all_residues_2rh1_3sn6_under_cutoff6A_regularization_wolf_autoShrinkage_rho0pt01/clusterer_tICs_1_2_25clusters_100samples_samples/cluster15_sample39.pdb

In [ ]:
graph_file = "%s/msm_lag_time%d_graph.graphml" % (tica_dir, lag_time)
construct_graph(msm_model_dir, clusterer_dir, n_clusters, 5, 5, graph_file, inactive = None, active = None, pnas_clusters_averages = None, tica_clusters_averages = None, docking=None, macrostate = None)


In [ ]:
from imp import reload
import custom_msm
reload(custom_msm)
from custom_msm import *
msm_file = msm_model_dir
sampled_frames_file = "%s/msm100_frames.h5" %tica_dir
msm_trajectory_filename = "%s/msm100_1000frames" %tica_dir
make_msm_trajectory(msm_file, projected_features_dir, traj_dir, sampled_frames_file, clusterer_dir, msm_trajectory_filename, 
                    n_clusters, start_cluster=22, n_steps=1000)

In [ ]:
mytraj = md.load("/home/amir/Post_Process/GPCR/MOR/LIG_path/BU_path/h5_trajectories/rep_1.h5")

In [ ]:
dir(mytraj)

In [ ]:
del mytraj

In [ ]:
subset = crystal_structure.atom_slice(range(0,400))
subset.xyz
print(subset.xyz)
distances = md.compute_contacts(subset)
print(distances)


In [ ]:
distances0 = distances[0]

In [ ]:
distances0 = np.nan_to_num(distances0)

In [ ]:
distances0

In [ ]:
np.where(distances0 > 0.0)

In [97]:
from msmbuilder.lumping.pcca_plus import PCCAPlus
n_macrostates = 50
lumper = PCCAPlus(n_macrostates)
msm_obj = verboseload(msm_model_dir)
lumper = lumper.from_msm(msm=msm_obj, n_macrostates=n_macrostates)


loading "/home/enf/b2ar_analysis/sparse-tICA_t5_n_components25all_residues_2rh1_3sn6_under_cutoff6A_regularization_wolf_autoShrinkage_rho0pt01/msm_lag_time10.h5"...


In [109]:
for cluster in inactive_clusters.index.values:
    if cluster in msm_obj.mapping_.keys():
        microstate = msm_obj.mapping_[cluster]
        macrostate = lumper.microstate_mapping_[microstate]
        if macrostate == 8: print(macrostate)